# Prerequisites:

## Drive:

In [ ]:
from google.colab import drive
drive.mount('/content/gdrive')

Mounted at /content/gdrive


## Libraries:

In [ ]:
!pip install pyperclip

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Preparing metadata (setup.py) ... done
  Created wheel for pyperclip: filename=pyperclip-1.8.2-py3-none-any.whl size=11124 sha256=46a3534c0d5177784e1c3f4c514836e5c00a2fa74b297288260d8ad7d086f2d1
  Stored in directory: /root/.cache/pip/wheels/04/24/fe/140a94a7f1036003ede94579e6b4227fe96c840c6f4dcbe307
Successfully built pyperclip


In [ ]:
import numpy as np
import pandas as pd

## Data:


In [ ]:
bureau = pd.read_csv('/content/gdrive/MyDrive/Colab Notebooks/home-credit/bureau.csv')
bal = pd.read_csv('/content/gdrive/MyDrive/Colab Notebooks/home-credit/bureau_bal.csv')
# application = pd.read_csv('/content/gdrive/MyDrive/Colab Notebooks/home-credit/application.csv')

In [ ]:

# def optimise_memory(data=None):
#     for col in data.columns:
#         if data[col].dtype == "int64":
#             data[col] = pd.to_numeric(data[col], downcast="integer")
#         # If the column has a float dtype, downcast it to the smallest float dtype
#         elif data[col].dtype == "float64":
#             data[col] = pd.to_numeric(data[col], downcast="float")
#         # If the column has an object dtype, try to convert it to a numeric dtype
#         elif data[col].dtype == "object":
#             data[col] = pd.to_numeric(data[col], errors="coerce")
#             # If there are any NaN values, fill them with a suitable substitute value
#             data[col] = data[col].fillna(0)
#         # If the column has any other dtype, leave it as is
#         else:
#             data[col] = data[col]

In [ ]:
# optimise_memory(bureau)
# optimise_memory(bal)

## Preset:


In [ ]:
pd.set_option('display.max_columns',None)
pd.set_option('display.max_rows',None)

# Changes in Data

In [ ]:
bureau = bureau.drop(columns=[
    'COUNT(bal)',#0 to calculate min max ,..
    'COUNT(bal WHERE STATUS = 0)',#0
    'COUNT(bal WHERE STATUS = 1)',#30
    'COUNT(bal WHERE STATUS = 2)',#60
    'COUNT(bal WHERE STATUS = 3)',#90
    'COUNT(bal WHERE STATUS = 4)',#120
    'COUNT(bal WHERE STATUS = 5)'#121
])

bureau = bureau.drop(columns=['Unnamed: 0'])
bal = bal.drop(columns=['Unnamed: 0'])

In [ ]:
bureau.head()

SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY DAYS_CREDIT  \
0      289470       5001071        Closed      currency 1  2015-03-02   
1      195162       5007519        Closed      currency 1  2015-03-02   
2      282691       5011980        Closed      currency 1  2015-03-02   
3      426357       5020085        Closed      currency 1  2015-03-02   
4      396604       5025742        Closed      currency 1  2015-03-02   

   CREDIT_DAY_OVERDUE DAYS_CREDIT_ENDDATE DAYS_ENDDATE_FACT  \
0                   0          2016-03-01        2016-03-01   
1                   0          2015-08-31        2015-09-01   
2                   0          2016-04-09        2016-03-26   
3                   0          2035-03-01        2021-07-31   
4                   0          2016-04-01        2016-03-03   

   AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
0                     NaN                   0        193999.5   
1                     NaN                   0        127017.0   
2                     NaN                   0        470412.0   
3                     NaN                   0       2407500.0   
4                     0.0                   0         47617.2   

   AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
0                  0.0                   NaN                     0.0   
1                  NaN                   NaN                     0.0   
2                  0.0                   NaN                     0.0   
3                  0.0                   0.0                     0.0   
4                  0.0                   0.0                     0.0   

       CREDIT_TYPE  DAYS_CREDIT_UPDATE  AMT_ANNUITY  
0  Consumer credit                 -60          NaN  
1  Consumer credit               -2737          NaN  
2  Consumer credit                -647          NaN  
3         Mortgage                 -32          NaN  
4  Consumer credit               -2555      45000.0

In [ ]:
bal.head()

SK_ID_BUREAU MONTHS_BALANCE  STATUS
0       5715448     2023-03-02       0
1       5715448     2023-02-02       0
2       5715448     2023-01-02       0
3       5715448     2022-12-02       0
4       5715448     2022-11-02       0

# EDA:

In [ ]:
# bal[bal['MONTHS_BALANCE']=='2023-02-02']['STATUS'].value_counts()

0      615277
30       5936
121       980
60        253
90         91
120        64
Name: STATUS, dtype: int64

In [ ]:
# bureau.CREDIT_CURRENCY.value_counts()

currency 1    1608409
currency 2       1149
currency 3        149
currency 4         10
Name: CREDIT_CURRENCY, dtype: int64

# Featuretools:

In [ ]:
!pip install featuretools

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 618.0/618.0 kB 16.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 235.5/235.5 kB 29.1 MB/s eta 0:00:00


In [ ]:
import featuretools as ft
es = ft.EntitySet(id='bureau')

In [ ]:
#@title Making sample data

es.add_dataframe(dataframe_name='bureau',dataframe=bureau,index='SK_ID_BUREAU',
                 time_index='DAYS_CREDIT')
curr_ids = pd.DataFrame(es['bureau']['SK_ID_CURR'].unique())
curr_ids = curr_ids.sample(n=5)
curr_ids.rename(columns = {0:'SK_ID_CURR'}, inplace = True)
es.add_dataframe(dataframe_name='curr_ids',dataframe=curr_ids,index='SK_ID_CURR')
es.add_dataframe(dataframe_name='bal',dataframe=bal,make_index=True,index='bal',
                 time_index='MONTHS_BALANCE')

Entityset: bureau
  DataFrames:
    bureau [Rows: 1609717, Columns: 17]
    curr_ids [Rows: 5, Columns: 1]
    bal [Rows: 27299925, Columns: 4]
  Relationships:
    No relationships

In [ ]:
r_curr_bureau = ft.Relationship(entityset=es,parent_dataframe_name='curr_ids',
                                parent_column_name='SK_ID_CURR',child_dataframe_name='bureau',
                                child_column_name='SK_ID_CURR')
r_bureau_bal = ft.Relationship(entityset=es,parent_dataframe_name='bureau',
                               parent_column_name='SK_ID_BUREAU',child_dataframe_name='bal',
                               child_column_name='SK_ID_BUREAU')

In [ ]:
es.add_relationships([r_curr_bureau,r_bureau_bal])

Entityset: bureau
  DataFrames:
    bureau [Rows: 1609717, Columns: 17]
    curr_ids [Rows: 5, Columns: 1]
    bal [Rows: 27299925, Columns: 4]
  Relationships:
    bureau.SK_ID_CURR -> curr_ids.SK_ID_CURR
    bal.SK_ID_BUREAU -> bureau.SK_ID_BUREAU

In [ ]:
es.add_interesting_values(verbose=True,
                          dataframe_name='bureau')
# es.add_interesting_values(verbose=True,
#                           dataframe_name='bal',
#                           values={'STATUS':['0','1','5','2','3','4']})

2023-06-15 05:36:10,888 featuretools.entityset - INFO    Column CREDIT_ACTIVE: Marking Closed as an interesting value
2023-06-15 05:36:10,889 featuretools.entityset - INFO    Column CREDIT_ACTIVE: Marking Active as an interesting value
2023-06-15 05:36:10,892 featuretools.entityset - INFO    Column CREDIT_ACTIVE: Marking Sold as an interesting value
2023-06-15 05:36:10,893 featuretools.entityset - INFO    Column CREDIT_ACTIVE: Marking Bad debt as an interesting value
2023-06-15 05:36:10,894 featuretools.entityset - INFO    Column CREDIT_CURRENCY: Marking currency 1 as an interesting value
2023-06-15 05:36:10,895 featuretools.entityset - INFO    Column CREDIT_CURRENCY: Marking currency 2 as an interesting value
2023-06-15 05:36:10,896 featuretools.entityset - INFO    Column CREDIT_CURRENCY: Marking currency 3 as an interesting value
2023-06-15 05:36:10,897 featuretools.entityset - INFO    Column CREDIT_CURRENCY: Marking currency 4 as an interesting value
2023-06-15 05:36:10,898 featuret

In [ ]:
es.add_last_time_indexes(['bureau','bal'])

In [ ]:
curr_ids.head()

SK_ID_CURR _ft_last_time
133513      133513    2022-10-30
274783      274783    2019-12-20
350477      350477    2022-03-03
269560      269560    2023-03-02
233696      233696    2023-03-02

In [ ]:
#@title DFS

feature_matrix,feature_names =  ft.dfs(entityset=es,
                                       target_dataframe_name = 'curr_ids',
                                    #    cutoff_time = pd.Timestamp('1997-12-31'),
                                    #    instance_ids = list(es['curr_ids']['SK_ID_CURR']),
                                       agg_primitives = ['sum'],
                                       trans_primitives = [ft.primitives.DivideNumeric()],
                                    #    groupby_trans_primitives=['equal','not_equal'],
                                    #    allowed_paths=None,
                                       max_depth=1,
                                    #    ignore_dataframes=['curr_ids'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS','CNT_DPD_91_120','CNT_DPD_1_30','CNT_DPD_61_90','CNT_DPD_120_PLUS','CNT_DPD_31_60','CNT_NO_DPD']},
                                    #    primitive_options=None,
                                    #    seed_features=None,
                                    #    drop_contains=['trans.date'],
                                    #    drop_exact=['AVG_TIME_BETWEEN(trans.date)'],
                                       where_primitives=['sum'],
                                    #    max_features=1200,
                                    #    features_only=True,
                                    #    cutoff_time_in_index=True,
                                    #    training_window = '1 months',
                                    #    approximate=None,
                                    #    save_progress=None,
                                    #    n_jobs=-1,
                                       chunk_size=100,
                                    #    dask_kwargs=None,
                                    #    return_types=None,
                                    #    progress_callback=None,
                                    #    include_cutoff_time=None,
                                       verbose=True)

/usr/local/lib/python3.9/dist-packages/featuretools/synthesis/dfs.py:321: UnusedPrimitiveWarning: Some specified primitives were not used during DFS:
  trans_primitives: ['divide_numeric']
This may be caused by a using a value of max_depth that is too small, not setting interesting values, or it may indicate no compatible columns for the primitive were found in the data. If the DFS call contained multiple instances of a primitive in the list above, none of them were used.
  warnings.warn(warning_msg, UnusedPrimitiveWarning)


Built 126 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
feature_matrix

SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
240020                     108216.0                                 0.0   
146559                          0.0                             27526.5   
175677                      63355.5                                 0.0   
204001                     190777.5                                 0.0   
133858                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
240020                    1.431097e+06                         946134.0   
146559                    3.285000e+05                              0.0   
175677                    2.555204e+06                         396535.5   
204001                    1.304726e+07                        3587260.5   
133858                    1.199367e+06                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
240020                                   0.0   
146559                                   0.0   
175677                                   0.0   
204001                                   0.0   
133858                              283500.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
240020                                     0.0   
146559                                     0.0   
175677                                     0.0   
204001                                     0.0   
133858                                     0.0   

            SUM(bureau.CNT_CREDIT_PROLONG)  SUM(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                                   
240020                                 0.0                             0.0   
146559                                 0.0                             0.0   
175677                                 0.0                             0.0   
204001                                 0.0                             0.0   
133858                                 0.0                             0.0   

            SUM(bureau.DAYS_CREDIT_UPDATE)  \
SK_ID_CURR                                   
240020                             -1999.0   
146559                               -76.0   
175677                             -9753.0   
204001                             -3068.0   
133858                             -2955.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Car loan)  \
SK_ID_CURR                                                         
240020                                                    0.0      
146559                                                    0.0      
175677                                                    0.0      
204001                                                    0.0      
133858                                                    0.0      

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                               
240020                                                    0.0            
146559                                                    0.0            
175677                                                    0.0            
204001                                                    0.0            
133858                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                          
240020                                                    0.0       
146559                                                    0.0       
175677                                                    0.0       
204001                                                    0.0

## COUNT Varaibles

In [ ]:
#@title Total Count Variables:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      where_primitives=[],
                                      verbose = True)

Built 1 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total Count for each PRODUCT:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CREDIT_ACTIVE','CREDIT_CURRENCY']},
                                      where_primitives=['count'],
                                      verbose = True)
feature_matrix.to_csv()

Built 6 features
Elapsed: 00:00 | Progress: 100%|██████████


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                     
406589                  1                                                  0   
342262                  5                                                  3   
432269                  1                                                  0   
400322                  1                                                  1   
286684                  1                                                  0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
406589                                                0   
342262                                                0   
432269                                                0   
400322                                                0   
286684                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                               
406589                                               0   
342262                                               0   
432269                                               0   
400322                                               0   
286684                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
406589                                                  0   
342262                                                  2   
432269                                                  1   
400322                                                  0   
286684                                                  1   

            COUNT(bureau WHERE CREDIT_TYPE = Car loan)  
SK_ID_CURR                                              
406589                                               1  
342262                                               0  
432269                                               0  
400322                                               0  
286684                                               0

In [ ]:
#@title Total Count for each CREDIT_ACTIVE status:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CREDIT_TYPE','CREDIT_CURRENCY']},
                                      where_primitives=['count'],
                                      verbose = True)

Built 5 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
feature_matrix

COUNT(bureau)  COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                                              
240020                  4                                           3   
146559                  2                                           0   
175677                  8                                           7   
204001                  6                                           3   
133858                  6                                           3   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
240020                                             0   
146559                                             0   
175677                                             0   
204001                                             0   
133858                                             1   

            COUNT(bureau WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                 
240020                                                 0   
146559                                                 0   
175677                                                 0   
204001                                                 0   
133858                                                 0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  
SK_ID_CURR                                              
240020                                               1  
146559                                               2  
175677                                               1  
204001                                               3  
133858                                               2

In [ ]:
#@title Total Count for each CREDIT_CURRENCY type:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CREDIT_TYPE','CREDIT_ACTIVE']},
                                      where_primitives=['count'],
                                      verbose = True)

Built 5 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
feature_matrix

COUNT(bureau)  COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                                    
240020                  4                                                 0   
146559                  2                                                 0   
175677                  8                                                 0   
204001                  6                                                 0   
133858                  6                                                 0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                                                     
240020                                                     0   
146559                                                     0   
175677                                                     0   
204001                                                     0   
133858                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
240020                                                     0   
146559                                                     0   
175677                                                     0   
204001                                                     0   
133858                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 1)  
SK_ID_CURR                                                    
240020                                                     4  
146559                                                     2  
175677                                                     8  
204001                                                     6  
133858                                                     6

In [ ]:
#@title COUNT of Trades in Last 3 Months

# Count of trades for last 3 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 3 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                    #   ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '3 months',
                                      verbose = True)
feature_matrix.head()

Built 28 features
Elapsed: 00:03 | Progress: 100%|██████████


COUNT(bureau)  COUNT(bal)  \
SK_ID_CURR                              
406589                  0           0   
342262                  0           0   
432269                  0           0   
400322                  1           3   
286684                  1           3   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
406589                                                      0   
342262                                                      0   
432269                                                      0   
400322                                                      1   
286684                                                      0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                 
406589                                                 0   
342262                                                 0   
432269                                                 0   
400322                                                 0   
286684                                                 0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
406589                                                0   
342262                                                0   
432269                                                0   
400322                                                0   
286684                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                               
406589                                               0   
342262                                               0   
432269                                               0   
400322                                               0   
286684                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
406589                                             0   
342262                                             0   
432269                                             0   
400322                                             0   
286684                                             0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
406589                                                  0   
342262                                                  0   
432269                                                  0   
400322                                                  0   
286684                                                  1   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                                                     
406589                                                     0   
342262                                                     0   
432269                                                     0   
400322                                                     0   
286684                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
406589                                               0   
342262                                               0   
432269                                               0   
400322                                               1   
286684                                               1   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
406589                                                     0   
342262                                                     0   
432269                                                     0   
400322                       

In [ ]:
#@title COUNT of Trades in Last 6 Months

# Count of trades for last 6 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 6 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '6 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  1                                           0   
159132                  0                                           0   
282545                  1                                           0   
226878                  0                                           0   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      1   
159132                                                      0   
282545                                                      1   
226878                                                      0   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               0   
159132                                               0   
282545                                               0   
226878                                               0   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               1   
159132                                               0   
282545                                               1   
226878                                               0   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 9 Months

# Count of trades for last 9 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 9 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '9 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  2                                           0   
159132                  0                                           0   
282545                  1                                           0   
226878                  0                                           0   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      2   
159132                                                      0   
282545                                                      1   
226878                                                      0   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               0   
159132                                               0   
282545                                               0   
226878                                               0   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               0   
282545                                               1   
226878                                               0   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 12 Months

# Count of trades for last 12 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 12 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '12 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  4                                           0   
159132                  3                                           0   
282545                  1                                           0   
226878                  0                                           0   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      4   
159132                                                      3   
282545                                                      1   
226878                                                      0   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               0   
282545                                               0   
226878                                               0   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               1   
226878                                               0   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 15 Months

# Count of trades for last 15 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 15 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '15 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  4                                           0   
159132                  3                                           0   
282545                  2                                           0   
226878                  1                                           0   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      4   
159132                                                      3   
282545                                                      2   
226878                                                      1   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               0   
282545                                               0   
226878                                               0   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               2   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 18 Months

# Count of trades for last 18 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 18 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '18 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  4                                           0   
159132                  3                                           0   
282545                  2                                           0   
226878                  2                                           0   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      4   
159132                                                      3   
282545                                                      2   
226878                                                      2   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               0   
282545                                               0   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               2   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 21 Months

# Count of trades for last 21 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 21 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '21 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  4                                           0   
159132                  3                                           0   
282545                  2                                           0   
226878                  2                                           0   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      4   
159132                                                      3   
282545                                                      2   
226878                                                      2   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               0   
282545                                               0   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               2   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 24 Months

# Count of trades for last 24 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 24 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '24 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  4                                           0   
159132                  3                                           0   
282545                  2                                           0   
226878                  2                                           0   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      4   
159132                                                      3   
282545                                                      2   
226878                                                      2   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               0   
282545                                               0   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               2   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 27 Months

# Count of trades for last 27 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 27 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '27 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  5                                           0   
159132                  3                                           0   
282545                  2                                           0   
226878                  3                                           1   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      5   
159132                                                      3   
282545                                                      2   
226878                                                      2   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               3   
159132                                               0   
282545                                               0   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               2   
226878                                               2   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 30 Months

# Count of trades for last 30 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 30 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      where_primitives=['count'],
                                      training_window = '30 months',
                                      verbose = True)
feature_matrix.head()

Built 28 features
Elapsed: 00:00 | Progress: 100%|██████████


COUNT(bureau)  COUNT(bal)  \
SK_ID_CURR                              
406589                  0           0   
342262                  2           0   
432269                  1           0   
400322                  1           7   
286684                  1          30   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
406589                                                      0   
342262                                                      1   
432269                                                      0   
400322                                                      1   
286684                                                      0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                 
406589                                                 0   
342262                                                 0   
432269                                                 0   
400322                                                 0   
286684                                                 0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
406589                                                0   
342262                                                0   
432269                                                0   
400322                                                0   
286684                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                               
406589                                               0   
342262                                               0   
432269                                               0   
400322                                               0   
286684                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
406589                                             0   
342262                                             0   
432269                                             0   
400322                                             0   
286684                                             0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
406589                                                  0   
342262                                                  1   
432269                                                  1   
400322                                                  0   
286684                                                  1   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                                                     
406589                                                     0   
342262                                                     0   
432269                                                     0   
400322                                                     0   
286684                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
406589                                               0   
342262                                               2   
432269                                               1   
400322                                               1   
286684                                               1   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
406589                                                     0   
342262                                                     0   
432269                                                     0   
400322                       

In [ ]:
#@title COUNT of Trades in Last 33 Months

# Count of trades for last 33 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 33 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '33 months',
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


/usr/local/lib/python3.9/dist-packages/featuretools/entityset/entityset.py:1566: UserWarning: Using training_window but last_time_index is not set for dataframe bureau
  warnings.warn(


COUNT(bureau)  COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                              
285268                  6                                           0   
159132                  4                                           0   
282545                  2                                           0   
226878                  4                                           1   
380391                  0                                           0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      6   
159132                                                      4   
282545                                                      2   
226878                                                      3   
380391                                                      0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               4   
159132                                               1   
282545                                               0   
226878                                               2   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  0   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               2   
226878                                               2   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                                             0   
380391                                             0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                       

In [ ]:
#@title COUNT of Trades in Last 36 Months

# Count of trades for last 36 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 36 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['count'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['count'],
                                      training_window = '36 months',
                                      verbose = True)
feature_matrix.head()

Built 28 features
Elapsed: 00:01 | Progress: 100%|██████████


COUNT(bureau)  COUNT(bal)  \
SK_ID_CURR                              
285268                  9         198   
159132                  8         211   
282545                  2           0   
226878                  6         139   
380391                  3         108   

            COUNT(bureau WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                               
285268                                               0   
159132                                               0   
282545                                               0   
226878                                               1   
380391                                               0   

            COUNT(bureau WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                      
285268                                                      9   
159132                                                      8   
282545                                                      2   
226878                                                      4   
380391                                                      3   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                     
285268                                                     0   
159132                                                     0   
282545                                                     0   
226878                                                     0   
380391                                                     0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                               
285268                                               7   
159132                                               5   
282545                                               0   
226878                                               3   
380391                                               3   

            COUNT(bureau WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                
285268                                                0   
159132                                                0   
282545                                                0   
226878                                                0   
380391                                                0   

            COUNT(bureau WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                  
285268                                                  0   
159132                                                  0   
282545                                                  0   
226878                                                  1   
380391                                                  0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                               
285268                                               2   
159132                                               3   
282545                                               2   
226878                                               3   
380391                                               0   

            COUNT(bureau WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                             
285268                                             0   
159132                                             0   
282545                                             0   
226878                     

In [ ]:
# bureau[bureau['SK_ID_CURR']==226878]
# bal[bal['SK_ID_BUREAU']==5788261]

## AMOUNT Variables

In [ ]:
#@title Total amount of loans for each person:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'CREDIT_ACTIVE', 'CREDIT_CURRENCY','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'AMT_CREDIT_MAX_OVERDUE', 'CNT_CREDIT_PROLONG','AMT_CREDIT_SUM_DEBT', 'AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_OVERDUE', 'CREDIT_TYPE', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=[],
                                      verbose = True)

Built 1 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total amount of Loan for Each product:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'CREDIT_ACTIVE', 'CREDIT_CURRENCY','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'AMT_CREDIT_MAX_OVERDUE', 'CNT_CREDIT_PROLONG','AMT_CREDIT_SUM_DEBT', 'AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_OVERDUE', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)

Built 6 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total amount of loan for each CREDIT_ACTIVE status:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'CREDIT_TYPE', 'CREDIT_CURRENCY','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'AMT_CREDIT_MAX_OVERDUE', 'CNT_CREDIT_PROLONG','AMT_CREDIT_SUM_DEBT', 'AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_OVERDUE', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)

Built 5 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total amount of loan for each CREDIT_CURRENCY type:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'CREDIT_ACTIVE', 'CREDIT_TYPE','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'AMT_CREDIT_MAX_OVERDUE', 'CNT_CREDIT_PROLONG','AMT_CREDIT_SUM_DEBT', 'AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_OVERDUE', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)
feature_matrix.head()

Built 5 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_CREDIT_SUM)  \
SK_ID_CURR                               
441836                       258786.00   
309469                      3408849.00   
193397                      2051286.48   
328632                       848347.56   
184776                      4368015.36   

            SUM(bureau.AMT_CREDIT_SUM WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                                  
441836                                                    0.0               
309469                                                    0.0               
193397                                                    0.0               
328632                                                    0.0               
184776                                                    0.0               

            SUM(bureau.AMT_CREDIT_SUM WHERE CREDIT_CURRENCY = currency 1)  \
SK_ID_CURR                                                                  
441836                                              258786.00               
309469                                             3408849.00               
193397                                             2051286.48               
328632                                              848347.56               
184776                                             4368015.36               

            SUM(bureau.AMT_CREDIT_SUM WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                                                                  
441836                                                    0.0               
309469                                                    0.0               
193397                                                    0.0               
328632                                                    0.0               
184776                                                    0.0               

            SUM(bureau.AMT_CREDIT_SUM WHERE CREDIT_CURRENCY = currency 4)  
SK_ID_CURR                                                                 
441836                                                    0.0              
309469                                                    0.0              
193397                                                    0.0              
328632                                                    0.0              
184776                                                    0.0

In [ ]:
bureau.columns

Index(['SK_ID_CURR', 'SK_ID_BUREAU', 'CREDIT_ACTIVE', 'CREDIT_CURRENCY',
       'DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE',
       'DAYS_ENDDATE_FACT', 'AMT_CREDIT_MAX_OVERDUE', 'CNT_CREDIT_PROLONG',
       'AMT_CREDIT_SUM', 'AMT_CREDIT_SUM_DEBT', 'AMT_CREDIT_SUM_LIMIT',
       'AMT_CREDIT_SUM_OVERDUE', 'CREDIT_TYPE', 'DAYS_CREDIT_UPDATE',
       'AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30',
       'CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD',
       '_ft_last_time'],
      dtype='object')

In [ ]:
#@title Total amount of maximal overdue & for each Product, Credit_Active and  Credit_Currency type:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'AMT_CREDIT_SUM', 'DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE', 'DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG','AMT_CREDIT_SUM_DEBT', 'AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_OVERDUE', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total amount of current debt on credit bureua & for each Product, Credit_Active and Credit_Currency type:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'AMT_CREDIT_SUM', 'AMT_CREDIT_MAX_OVERDUE','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE', 'DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_OVERDUE', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total amount of credit card limit & for each Product, Credit_Active and Credit_Currency type:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'AMT_CREDIT_SUM', 'AMT_CREDIT_MAX_OVERDUE','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE', 'DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'AMT_CREDIT_SUM_DEBT','AMT_CREDIT_SUM_OVERDUE', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total amount of current overdue on Credit Bureau & for each Product, Credit_Active and Credit_Currency type:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'AMT_CREDIT_SUM', 'AMT_CREDIT_MAX_OVERDUE','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE', 'DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'AMT_CREDIT_SUM_DEBT','AMT_CREDIT_SUM_LIMIT', 'DAYS_CREDIT_UPDATE','AMT_ANNUITY', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Total amount of Annuity of Credit Bureau & for each Product, Credit_Active and Credit_Currency type:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['SK_ID_CURR', 'SK_ID_BUREAU', 'AMT_CREDIT_SUM', 'AMT_CREDIT_MAX_OVERDUE','DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE', 'DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'AMT_CREDIT_SUM_DEBT','AMT_CREDIT_SUM_LIMIT', 'DAYS_CREDIT_UPDATE','AMT_CREDIT_SUM_OVERDUE', 'CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      verbose = True)

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


In [ ]:
#@title Amount of Trades in Last 3 Months

# Amount of trades for last 3 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 3 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '3 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                            0.00                              0.0   
193397                            0.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 6 Months

# Amount of trades for last 6 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 6 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '6 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:01 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                            0.00                              0.0   
193397                            0.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 9 Months

# Amount of trades for last 9 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 9 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '9 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                            0.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 12 Months

# Amount of trades for last 12 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 12 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '12 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 15 Months

# Amount of trades for last 15 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 15 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '15 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 18 Months

# Amount of trades for last 18 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 18 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '18 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 21 Months

# Amount of trades for last 21 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 21 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '21 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:03 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
271122                        0.000                                 0.0   
441952                        0.000                                 0.0   
243144                    65694.825                                 0.0   
165690                        0.000                                 0.0   
232042                        0.000                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
271122                        102771.0                              0.0   
441952                        294750.0                         242577.0   
243144                       2751768.0                        1067269.5   
165690                        225000.0                         165433.5   
232042                        450000.0                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
271122                                   0.0   
441952                                   0.0   
243144                                   0.0   
165690                                   0.0   
232042                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
271122                                     0.0   
441952                                     0.0   
243144                                     0.0   
165690                                     0.0   
232042                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
271122                                                  0.000             
441952                                                  0.000             
243144                                              65694.825             
165690                                                  0.000             
232042                                                  0.000             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
271122                                                    0.0      
441952                                                    0.0      
243144                                                    0.0      
165690                                                    0.0      
232042                                                    0.0      

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
271122                                                    0.0        
441952                                                    0.0        
243144                                                    0.0        
165690                                                    0.0        
232042                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 1)  \
SK_ID_CURR                                                               
271122                                                  0.000            
441952                                                  0.000            
243144                                              65694.825            
165690                                                  0.000            
232042                                                  0.000            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
271122                                                    0.0            
441952                               

In [ ]:
#@title Amount of Trades in Last 24 Months

# Amount of trades for last 24 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 24 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '24 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 27 Months

# Amount of trades for last 27 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 27 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '27 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 30 Months

# Amount of trades for last 30 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 30 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '30 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 33 Months

# Amount of trades for last 33 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 33 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '33 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

In [ ]:
#@title Amount of Trades in Last 36 Months

# Amount of trades for last 36 months (total and for each category). This result is with max_depth = 1.
# With max_depth = 2, we get count of individual transaction for 36 months (total and for each category).

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time = pd.Timestamp('2023-03-02'),
                                      agg_primitives = ['sum'],
                                      trans_primitives = [],
                                      max_depth=2,
                                      ignore_columns={'bureau':['DAYS_CREDIT', 'CREDIT_DAY_OVERDUE', 'DAYS_CREDIT_ENDDATE','DAYS_ENDDATE_FACT', 'CNT_CREDIT_PROLONG', 'DAYS_CREDIT_UPDATE','CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD'],
                                                      'bal':['STATUS']},
                                      where_primitives=['sum'],
                                      training_window = '36 months',
                                      verbose = True)
feature_matrix.head()

Built 168 features
Elapsed: 00:00 | Progress: 100%|██████████


SUM(bureau.AMT_ANNUITY)  SUM(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
441836                          0.0                                 0.0   
309469                          0.0                                 0.0   
193397                          0.0                                 0.0   
328632                      12933.0                                 0.0   
184776                          0.0                                 0.0   

            SUM(bureau.AMT_CREDIT_SUM)  SUM(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
441836                            0.00                              0.0   
309469                      3232611.00                        3145014.0   
193397                       101880.00                              0.0   
328632                       848347.56                          34632.0   
184776                      4368015.36                              0.0   

            SUM(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
441836                                   0.0   
309469                                   0.0   
193397                                   0.0   
328632                                   0.0   
184776                                   0.0   

            SUM(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
441836                                     0.0   
309469                                     0.0   
193397                                     0.0   
328632                                     0.0   
184776                                     0.0   

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                            
441836                                                    0.0         
309469                                                    0.0         
193397                                                    0.0         
328632                                                    0.0         
184776                                                    0.0         

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                               
441836                                                    0.0            
309469                                                    0.0            
193397                                                    0.0            
328632                                                    0.0            
184776                                                    0.0            

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
441836                                                    0.0        
309469                                                    0.0        
193397                                                    0.0        
328632                                                    0.0        
184776                                                    0.0        

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
441836                                                    0.0             
309469                                                    0.0             
193397                                                    0.0             
328632                                                12933.0             
184776                                                    0.0             

            SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                         
441836                                                    0.0      
309469                            

## TIME Variables:

In [ ]:
#@title Time since recent:
feature_matrix,feature_names=ft.dfs(entityset=es,
                                    target_dataframe_name='curr_ids',
                                    agg_primitives=[ft.primitives.TimeSinceLast(unit='days')],
                                    trans_primitives=[],
                                    max_depth=1,
                                    ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                    where_primitives=[ft.primitives.TimeSinceLast(unit='days')],
                                    verbose=True)
feature_matrix.head()

Built 14 features
Elapsed: 00:00 | Progress: 100%|██████████


TIME_SINCE_LAST(bureau.DAYS_CREDIT, unit=days)  \
SK_ID_CURR                                                   
266187                                          109.220073   
294085                                          345.220073   
448569                                         1504.220073   
152668                                          121.220073   
238989                                          987.220073   

            TIME_SINCE_LAST(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Closed, unit=days)  \
SK_ID_CURR                                                                                
266187                                             540.220073                             
294085                                            1074.220073                             
448569                                            1504.220073                             
152668                                                    NaN                             
238989                                            2227.220073                             

            TIME_SINCE_LAST(bureau.DAYS_CREDIT WHERE CREDIT_TYPE = Car loan, unit=days)  \
SK_ID_CURR                                                                                
266187                                                    NaN                             
294085                                                    NaN                             
448569                                                    NaN                             
152668                                                    NaN                             
238989                                                    NaN                             

            TIME_SINCE_LAST(bureau.DAYS_CREDIT WHERE CREDIT_TYPE = Mortgage, unit=days)  \
SK_ID_CURR                                                                                
266187                                                    NaN                             
294085                                                    NaN                             
448569                                                    NaN                             
152668                                                    NaN                             
238989                                                    NaN                             

            TIME_SINCE_LAST(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Sold, unit=days)  \
SK_ID_CURR                                                                              
266187                                                    NaN                           
294085                                                    NaN                           
448569                                                    NaN                           
152668                                                    NaN                           
238989                                                    NaN                           

            TIME_SINCE_LAST(bureau.DAYS_CREDIT WHERE CREDIT_CURRENCY = currency 2, unit=days)  \
SK_ID_CURR                                                                                      
266187                                                    NaN                                   
294085                                                    NaN                                   
448569                                                    NaN                                   
152668                                                    NaN                                   
238989                                                    NaN                                   

            TIME_SINCE_LAST(bureau.DAYS_CREDIT WHERE CREDIT_TYPE = Consumer credit, unit=days)  \
SK_ID_CURR                                                                                       
266187                                             109.220073                                    
294085                                             345.220073    

In [ ]:
#@title Time since oldest:
feature_matrix,feature_names=ft.dfs(entityset=es,
                                    target_dataframe_name='curr_ids',
                                    agg_primitives=[ft.primitives.TimeSinceFirst(unit='days')],
                                    trans_primitives=[],
                                    max_depth=2,
                                    ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                    where_primitives=[ft.primitives.TimeSinceFirst(unit='days')],
                                    verbose=True)
feature_matrix.head()

Built 42 features
Elapsed: 00:06 | Progress: 100%|██████████


TIME_SINCE_FIRST(bureau.DAYS_CREDIT, unit=days)  \
SK_ID_CURR                                                    
184577                                           1758.51787   
364871                                            579.51787   
283440                                           2471.51787   
341331                                           2813.51787   
247141                                           1455.51787   

            TIME_SINCE_FIRST(bal.MONTHS_BALANCE, unit=days)  \
SK_ID_CURR                                                    
184577                                           1756.51787   
364871                                            568.51787   
283440                                           2455.51787   
341331                                                  NaN   
247141                                                  NaN   

            TIME_SINCE_FIRST(bureau.DAYS_CREDIT WHERE CREDIT_CURRENCY = currency 3, unit=days)  \
SK_ID_CURR                                                                                       
184577                                                    NaN                                    
364871                                                    NaN                                    
283440                                                    NaN                                    
341331                                                    NaN                                    
247141                                                    NaN                                    

            TIME_SINCE_FIRST(bureau.DAYS_CREDIT WHERE CREDIT_CURRENCY = currency 4, unit=days)  \
SK_ID_CURR                                                                                       
184577                                                    NaN                                    
364871                                                    NaN                                    
283440                                                    NaN                                    
341331                                                    NaN                                    
247141                                                    NaN                                    

            TIME_SINCE_FIRST(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Bad debt, unit=days)  \
SK_ID_CURR                                                                                   
184577                                                    NaN                                
364871                                                    NaN                                
283440                                                    NaN                                
341331                                                    NaN                                
247141                                                    NaN                                

            TIME_SINCE_FIRST(bureau.DAYS_CREDIT WHERE CREDIT_TYPE = Microloan, unit=days)  \
SK_ID_CURR                                                                                  
184577                                                    NaN                               
364871                                                    NaN                               
283440                                                    NaN                               
341331                                                    NaN                               
247141                                                    NaN                               

            TIME_SINCE_FIRST(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Closed, unit=days)  \
SK_ID_CURR                                                                                 
184577                                             1758.51787                              
364871                                              579.51787                              
283440                                             2471.51787              

In [ ]:
#@title ??? RollingCount

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['count','mean'],
                                      trans_primitives = ['rolling_count','rolling_mean','rolling_max'],
                                      max_depth=3,
                                    #   ignore_dataframes=['bureau'],
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=[],
                                      verbose = True)
feature_matrix.head()

Built 52 features
Elapsed: 2:58:37 | Progress:  40%|███▉      

In [ ]:
#@title ??? Age

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'bureau',
                                      agg_primitives = [],
                                      trans_primitives = [ft.primitives.DateToHoliday(country='IN')],
                                      max_depth=1,
                                    #   ignore_dataframes=['bureau'],
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=[],
                                      verbose = True)
feature_matrix.head()

## CORRELATION Variables:

There are in total 1134 variables in this section:

- Correlation: **1008**
- AutoCorrelation: **126**

In [ ]:
#@title Correlation
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['correlation'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['correlation'],
                                      verbose = True)
feature_matrix

Built 1008 features
Elapsed: 00:00 | Progress:  16%|█▌        

/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/n

Elapsed: 00:00 | Progress:  75%|███████▌  

/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/n

Elapsed: 00:00 | Progress:  94%|█████████▍

/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)


Elapsed: 00:00 | Progress: 100%|██████████


CORRELATION(bureau.AMT_ANNUITY, AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                            
359976                                                    NaN         
109974                                                    NaN         
210111                                                    NaN         
416402                                                    NaN         
433446                                                    NaN         

            CORRELATION(bureau.AMT_ANNUITY, AMT_CREDIT_SUM)  \
SK_ID_CURR                                                    
359976                                                  NaN   
109974                                                  NaN   
210111                                                  NaN   
416402                                                  NaN   
433446                                                  NaN   

            CORRELATION(bureau.AMT_ANNUITY, AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                         
359976                                                    NaN      
109974                                                    NaN      
210111                                                    NaN      
416402                                                    NaN      
433446                                                    NaN      

            CORRELATION(bureau.AMT_ANNUITY, AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                                          
359976                                                    NaN       
109974                                                    NaN       
210111                                                    NaN       
416402                                                    NaN       
433446                                                    NaN       

            CORRELATION(bureau.AMT_ANNUITY, AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                                            
359976                                                    NaN         
109974                                                    NaN         
210111                                                    NaN         
416402                                                    NaN         
433446                                                    NaN         

            CORRELATION(bureau.AMT_ANNUITY, CNT_CREDIT_PROLONG)  \
SK_ID_CURR                                                        
359976                                                    NaN     
109974                                                    NaN     
210111                                                    NaN     
416402                                                    NaN     
433446                                                    NaN     

            CORRELATION(bureau.AMT_ANNUITY, CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                        
359976                                                    NaN     
109974                                                    NaN     
210111                                                    NaN     
416402                                                    NaN     
433446                                                    NaN     

            CORRELATION(bureau.AMT_ANNUITY, DAYS_CREDIT_UPDATE)  \
SK_ID_CURR                                                        
359976                                                    NaN     
109974                                                    NaN     
210111                                                    NaN     
416402                                                    NaN     
433446                                                    NaN     

            CORRELATION(bureau.AMT_CREDIT_MAX_OVERDUE, AMT_ANNUITY)  \
SK_ID_CURR                                                            
359976                                                    NaN

In [ ]:
#@title AutoCorrelation
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['auto_correlation'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['auto_correlation'],
                                      verbose = True)
feature_matrix

Built 126 features
Elapsed: 00:00 | Progress:  50%|████▉     

/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2821: RuntimeWarning: Degrees of freedom <= 0 for slice
  c = cov(x, y, rowvar, dtype=dtype)
/usr/local/lib/python3.9/dist-packages/numpy/lib/function_base.py:2680: RuntimeWarning: divide by zero encountered in true_divide
  c *= np.true_divide(1, fact)
/usr/local/lib/python3.9/dist-packages/n

Elapsed: 00:00 | Progress: 100%|██████████


AUTO_CORRELATION(bureau.AMT_ANNUITY)  \
SK_ID_CURR                                         
359976                                       0.0   
109974                                       0.0   
210111                                       0.0   
416402                                       0.0   
433446                                       0.0   

            AUTO_CORRELATION(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                    
359976                                                  0.0   
109974                                                  0.0   
210111                                                  0.0   
416402                                                  0.0   
433446                                                  0.0   

            AUTO_CORRELATION(bureau.AMT_CREDIT_SUM)  \
SK_ID_CURR                                            
359976                                         -1.0   
109974                                          0.0   
210111                                          0.0   
416402                                          0.0   
433446                                          0.0   

            AUTO_CORRELATION(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                 
359976                                               0.0   
109974                                               0.0   
210111                                               0.0   
416402                                               0.0   
433446                                               0.0   

            AUTO_CORRELATION(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                                  
359976                                                0.0   
109974                                                0.0   
210111                                                0.0   
416402                                                0.0   
433446                                                0.0   

            AUTO_CORRELATION(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                                    
359976                                                  0.0   
109974                                                  0.0   
210111                                                  0.0   
416402                                                  0.0   
433446                                                  0.0   

            AUTO_CORRELATION(bureau.CNT_CREDIT_PROLONG)  \
SK_ID_CURR                                                
359976                                              0.0   
109974                                              0.0   
210111                                              0.0   
416402                                              0.0   
433446                                              0.0   

            AUTO_CORRELATION(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                
359976                                              0.0   
109974                                              0.0   
210111                                              0.0   
416402                                              0.0   
433446                                              0.0   

            AUTO_CORRELATION(bureau.DAYS_CREDIT_UPDATE)  \
SK_ID_CURR                                                
359976                                              1.0   
109974                                              0.0   
210111                                              0.0   
416402                                              0.0   
433446                                              0.0   

            AUTO_CORRELATION(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                             
359976                                                    0.0                          
109974                

## Volitility Variables:

There are in total 1137 features excluding the 126 features made using NumPeaks.

- Mean, Median & Mode: **281**
- Minimum & Maximum: **252**
- Skewness & Kurtosis: **252**
- StandardDeviaiton & Varaince: **252**
- AvgTimeBetween, TimeSinceFirst & TimeSinceLast: **42**
- AvgCountPerUnique: **29**
- NumPeaks: **126**
- Entropy: **29**

In [ ]:
#@title Mean, Median & Mode
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['mean','median','mode'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['mean','median','mode'],
                                      verbose = True)
feature_matrix

Built 281 features
Elapsed: 00:00 | Progress:  33%|███▎      

/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local

Elapsed: 00:00 | Progress:  95%|█████████▍

/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.10/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local

Elapsed: 00:00 | Progress: 100%|██████████


MEAN(bureau.AMT_ANNUITY)  MEAN(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                  
434360                           NaN                             20955.84   
316718                       28201.5                                 0.00   
315266                           NaN                                 0.00   
320673                        1595.7                                 0.00   
403530                           NaN                                  NaN   

            MEAN(bureau.AMT_CREDIT_SUM)  MEAN(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                  
434360                     3.926791e+05                      171508.42875   
316718                     1.566900e+06                       78870.37500   
315266                     1.040095e+05                           0.00000   
320673                     1.385294e+05                       59585.06250   
403530                     1.800000e+05                               NaN   

            MEAN(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                      
434360                                 3937.5   
316718                                    0.0   
315266                                    0.0   
320673                                    0.0   
403530                                    NaN   

            MEAN(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                        
434360                                      0.0   
316718                                      0.0   
315266                                      0.0   
320673                                      0.0   
403530                                      0.0   

            MEAN(bureau.CNT_CREDIT_PROLONG)  MEAN(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                                     
434360                             0.083333                              0.0   
316718                             0.000000                              0.0   
315266                             0.000000                              0.0   
320673                             0.000000                              0.0   
403530                             0.000000                              0.0   

            MEAN(bureau.DAYS_CREDIT_UPDATE)  MEDIAN(bureau.AMT_ANNUITY)  \
SK_ID_CURR                                                                
434360                               -561.5                         NaN   
316718                                -61.4                     11781.0   
315266                              -1170.6                         NaN   
320673                               -414.0                         0.0   
403530                                -15.0                         NaN   

            MEDIAN(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                          
434360                                   21427.02   
316718                                       0.00   
315266                                       0.00   
320673                                       0.00   
403530                                        NaN   

            MEDIAN(bureau.AMT_CREDIT_SUM)  MEDIAN(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                      
434360                        112633.2675                                 0.0   
316718                        157500.0000                             75406.5   
315266                         89946.0000                                 0.0   
320673                        157500.0000                              3951.0   
403530                        180000.0000                                 NaN   

            MEDIAN(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                        
434360                                      0.0   
316718                                      0.0   

In [ ]:
#@title Minimum & Maximum
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['min','max'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['min','max'],
                                      verbose = True)
feature_matrix

Built 252 features
Elapsed: 00:00 | Progress: 100%|██████████


MAX(bureau.AMT_ANNUITY)  MAX(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
217867                      11439.0                                 0.0   
386110                       6390.0                                 0.0   
245209                          NaN                                 0.0   
286017                          NaN                             23458.5   
371986                          NaN                                 NaN   

            MAX(bureau.AMT_CREDIT_SUM)  MAX(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
217867                        392400.0                         309847.5   
386110                        576000.0                              0.0   
245209                       1170000.0                          40059.0   
286017                       1012414.5                              0.0   
371986                       1462500.0                        1206765.0   

            MAX(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
217867                                   0.0   
386110                                   0.0   
245209                                   0.0   
286017                                   0.0   
371986                                   0.0   

            MAX(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
217867                                     0.0   
386110                                     0.0   
245209                                     0.0   
286017                                     0.0   
371986                                     0.0   

            MAX(bureau.CNT_CREDIT_PROLONG)  MAX(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                                   
217867                                 0.0                             0.0   
386110                                 0.0                             0.0   
245209                                 0.0                             0.0   
286017                                 0.0                             0.0   
371986                                 0.0                             0.0   

            MAX(bureau.DAYS_CREDIT_UPDATE)  MIN(bureau.AMT_ANNUITY)  \
SK_ID_CURR                                                            
217867                                -7.0                      0.0   
386110                               -24.0                      0.0   
245209                               -25.0                      NaN   
286017                             -1534.0                      NaN   
371986                                -7.0                      NaN   

            MIN(bureau.AMT_CREDIT_MAX_OVERDUE)  MIN(bureau.AMT_CREDIT_SUM)  \
SK_ID_CURR                                                                   
217867                                     0.0                     49792.5   
386110                                     0.0                     16371.0   
245209                                     0.0                     56385.0   
286017                                 23458.5                   1012414.5   
371986                                     NaN                     67500.0   

            MIN(bureau.AMT_CREDIT_SUM_DEBT)  MIN(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                                                      
217867                                  0.0                               0.0   
386110                                  0.0                               0.0   
245209                                  0.0                               0.0   
286017                                  0.0                               0.0   
371986                                  0.0                               0.0   

            MIN(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
217867      

In [ ]:
#@title Skewness & Kurtosis
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['skew','kurtosis'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['skew','kurtosis'],
                                      verbose = True)
feature_matrix

In [ ]:
#@title StandardDeviation & Variance
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['std','variance'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['std','variance'],
                                      verbose = True)
feature_matrix

Built 252 features
Elapsed: 00:00 | Progress: 100%|██████████


STD(bureau.AMT_ANNUITY)  STD(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
359976                          NaN                                 0.0   
109974                          NaN                                 NaN   
210111                          NaN                                 NaN   
416402                          NaN                                 NaN   
433446                          NaN                                 NaN   

            STD(bureau.AMT_CREDIT_SUM)  STD(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
359976                   247131.771153                    341579.244361   
109974                             NaN                              NaN   
210111                    38183.766184                     52792.238730   
416402                             NaN                              NaN   
433446                   389711.431703                         0.000000   

            STD(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
359976                                   0.0   
109974                                   NaN   
210111                                   0.0   
416402                                   NaN   
433446                                   0.0   

            STD(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
359976                                     0.0   
109974                                     NaN   
210111                                     0.0   
416402                                     NaN   
433446                                     0.0   

            STD(bureau.CNT_CREDIT_PROLONG)  STD(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                                   
359976                                 0.0                             0.0   
109974                                 NaN                             NaN   
210111                                 0.0                             0.0   
416402                                 NaN                             NaN   
433446                                 0.0                             0.0   

            STD(bureau.DAYS_CREDIT_UPDATE)  VARIANCE(bureau.AMT_ANNUITY)  \
SK_ID_CURR                                                                 
359976                         1160.939849                           NaN   
109974                                 NaN                           NaN   
210111                            0.000000                           NaN   
416402                                 NaN                           NaN   
433446                          702.635278                           NaN   

            VARIANCE(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                            
359976                                          0.0   
109974                                          NaN   
210111                                          NaN   
416402                                          NaN   
433446                                          NaN   

            VARIANCE(bureau.AMT_CREDIT_SUM)  \
SK_ID_CURR                                    
359976                         6.107411e+10   
109974                                  NaN   
210111                         1.458000e+09   
416402                                  NaN   
433446                         1.518750e+11   

            VARIANCE(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                         
359976                              1.166764e+11   
109974                                       NaN   
210111                              2.787020e+09   
416402                                       NaN   
433446                              0.000000e+00   

            VARIANCE(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                          
35997

In [ ]:
#@title AvgTimeBetween, TimeSinceFirst & TimeSinceLast
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = [ft.primitives.AvgTimeBetween(unit='days'),ft.primitives.TimeSinceFirst(unit='days'),ft.primitives.TimeSinceLast(unit='days')],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=[ft.primitives.AvgTimeBetween(unit='days'),ft.primitives.TimeSinceFirst(unit='days'),ft.primitives.TimeSinceLast(unit='days')],
                                      verbose = True)
feature_matrix

Built 42 features
Elapsed: 00:00 | Progress: 100%|██████████


AVG_TIME_BETWEEN(bureau.DAYS_CREDIT, unit=days)  \
SK_ID_CURR                                                    
217867                                           480.000000   
386110                                           349.800000   
245209                                           288.428571   
286017                                                  NaN   
371986                                           150.333333   

            TIME_SINCE_FIRST(bureau.DAYS_CREDIT, unit=days)  \
SK_ID_CURR                                                    
217867                                          2116.344085   
386110                                          2476.344085   
245209                                          2614.344085   
286017                                          2685.344085   
371986                                           672.344085   

            TIME_SINCE_LAST(bureau.DAYS_CREDIT, unit=days)  \
SK_ID_CURR                                                   
217867                                          676.344085   
386110                                          727.344085   
245209                                          595.344085   
286017                                         2685.344085   
371986                                          221.344085   

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Bad debt, unit=days)  \
SK_ID_CURR                                                                                   
217867                                                    NaN                                
386110                                                    NaN                                
245209                                                    NaN                                
286017                                                    NaN                                
371986                                                    NaN                                

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_CURRENCY = currency 4, unit=days)  \
SK_ID_CURR                                                                                       
217867                                                    NaN                                    
386110                                                    NaN                                    
245209                                                    NaN                                    
286017                                                    NaN                                    
371986                                                    NaN                                    

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_TYPE = Credit card, unit=days)  \
SK_ID_CURR                                                                                    
217867                                                    NaN                                 
386110                                                    NaN                                 
245209                                                  673.0                                 
286017                                                    NaN                                 
371986                                                    NaN                                 

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Active, unit=days)  \
SK_ID_CURR                                                                                 
217867                                             371.000000                              
386110                                                    NaN                              
245209                                             421.666667                              
286017                                                    NaN                              
371986                                             222.000000                              

            AVG_TIME_BETWEEN(bureau.

In [ ]:
#@title AvgCountPerUnique
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['average_count_per_unique'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['average_count_per_unique'],
                                      verbose = True)
feature_matrix

Built 29 features
Elapsed: 00:00 | Progress: 100%|██████████


AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_ACTIVE)  \
SK_ID_CURR                                                   
217867                                                1.00   
386110                                                1.50   
245209                                                2.00   
286017                                                0.25   
371986                                                1.00   

            AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_CURRENCY)  \
SK_ID_CURR                                                     
217867                                                  1.00   
386110                                                  1.50   
245209                                                  2.00   
286017                                                  0.25   
371986                                                  1.00   

            AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_TYPE)  \
SK_ID_CURR                                                 
217867                                          0.266667   
386110                                          0.400000   
245209                                          0.533333   
286017                                          0.066667   
371986                                          0.266667   

            AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                                                      
217867                                                    0.0                                   
386110                                                    0.0                                   
245209                                                    0.0                                   
286017                                                    0.0                                   
371986                                                    0.0                                   

            AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                                                   
217867                                                   0.25                                
386110                                                   0.00                                
245209                                                   0.50                                
286017                                                   0.00                                
371986                                                   0.25                                

            AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                                                 
217867                                                    0.0                              
386110                                                    0.0                              
245209                                                    0.0                              
286017                                                    0.0                              
371986                                                    0.0                              

            AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Car loan)  \
SK_ID_CURR                                                                                
217867                                                   0.00                             
386110                                                   0.00                             
245209                                                   0.00                             
286017                                                   0.25                             
371986                                                   0.00                             

            AVERAGE_COUNT_PER_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = cur

In [ ]:
#@title ??? NumPeaks
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['num_peaks'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['num_peaks'],
                                      verbose = True)
feature_matrix

Built 126 features
Elapsed: 00:00 | Progress: 100%|██████████


NUM_PEAKS(bureau.AMT_ANNUITY)  \
SK_ID_CURR                                  
359976                                  0   
109974                                  0   
210111                                  0   
416402                                  0   
433446                                  0   

            NUM_PEAKS(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                             
359976                                             0   
109974                                             0   
210111                                             0   
416402                                             0   
433446                                             0   

            NUM_PEAKS(bureau.AMT_CREDIT_SUM)  \
SK_ID_CURR                                     
359976                                     0   
109974                                     0   
210111                                     0   
416402                                     0   
433446                                     0   

            NUM_PEAKS(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                          
359976                                          0   
109974                                          0   
210111                                          0   
416402                                          0   
433446                                          0   

            NUM_PEAKS(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                           
359976                                           0   
109974                                           0   
210111                                           0   
416402                                           0   
433446                                           0   

            NUM_PEAKS(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                             
359976                                             0   
109974                                             0   
210111                                             0   
416402                                             0   
433446                                             0   

            NUM_PEAKS(bureau.CNT_CREDIT_PROLONG)  \
SK_ID_CURR                                         
359976                                         0   
109974                                         0   
210111                                         0   
416402                                         0   
433446                                         0   

            NUM_PEAKS(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                         
359976                                         0   
109974                                         0   
210111                                         0   
416402                                         0   
433446                                         0   

            NUM_PEAKS(bureau.DAYS_CREDIT_UPDATE)  \
SK_ID_CURR                                         
359976                                         0   
109974                                         0   
210111                                         0   
416402                                         0   
433446                                         0   

            NUM_PEAKS(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                      
359976                                                      0                   
109974                                                      0                   
210111                                                      0                   
416402                                                      0                   
433446                                                      0                   

            NUM_PEAKS(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                                 
359976 

In [ ]:
ft.primitives.entropy()

In [ ]:
#@title Entropy
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['entropy'],
                                      trans_primitives = [],
                                      max_depth=1,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['entropy'],
                                      verbose = True)
feature_matrix

Built 29 features
Elapsed: 00:00 | Progress: 100%|██████████


ENTROPY(bureau.CREDIT_ACTIVE)  ENTROPY(bureau.CREDIT_CURRENCY)  \
SK_ID_CURR                                                                   
209812                           0.500402                              0.0   
282145                           0.655482                              0.0   
264627                           0.610864                              0.0   
299134                           0.898205                              0.0   
292542                           0.500402                              0.0   

            ENTROPY(bureau.CREDIT_TYPE)  \
SK_ID_CURR                                
209812                         0.673012   
282145                         0.655482   
264627                         0.897946   
299134                         0.651757   
292542                         0.500402   

            ENTROPY(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                                     
209812                                                    NaN                  
282145                                                    NaN                  
264627                                                    NaN                  
299134                                                    NaN                  
292542                                                    NaN                  

            ENTROPY(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                                     
209812                                                    NaN                  
282145                                                    NaN                  
264627                                                    NaN                  
299134                                                    NaN                  
292542                                                    NaN                  

            ENTROPY(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Car loan)  \
SK_ID_CURR                                                               
209812                                                    NaN            
282145                                                    NaN            
264627                                                    NaN            
299134                                                    NaN            
292542                                                    NaN            

            ENTROPY(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                                  
209812                                               0.636514               
282145                                               0.562335               
264627                                               0.636514               
299134                                               0.673012               
292542                                               0.000000               

            ENTROPY(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                      
209812                                               0.000000                   
282145                                               0.682908                   
264627                                               0.450561                   
299134                                               0.936888                   
292542                                               0.562335                   

            ENTROPY(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                                                                     
209812                                                    NaN                  
282145                                                    NaN                  
264627                                                    NaN                  
299134        

## Ratio Variables:

In [ ]:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = ['sum'],
                                      trans_primitives = ['divide_numeric'],
                                      max_depth=3,
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30',
                                                                'CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['sum'],
                                      primitive_options={'divide_numeric':{'include_columns':{'bureau':['AMT_ANNUITY','CREDIT_TYPE']}},
                                                         'sum':{'include_columns':{'bureau':['AMT_ANNUITY','CREDIT_TYPE']}}},
                                      verbose = True)
feature_names

Built 126 features
Elapsed: 00:00 | Progress: 100%|██████████


[<Feature: SUM(bureau.AMT_ANNUITY)>,
 <Feature: SUM(bal.STATUS)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 4)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Car loan)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Sold)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 3)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 1)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Closed)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Microloan)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Active)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)>,
 <Feature: SUM(bal.bureau.AMT_ANNUITY)>,


In [ ]:
bureau.head()

SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY DAYS_CREDIT  \
5001071      289470       5001071        Closed      currency 1  2015-03-02   
5007519      195162       5007519        Closed      currency 1  2015-03-02   
5011980      282691       5011980        Closed      currency 1  2015-03-02   
5020085      426357       5020085        Closed      currency 1  2015-03-02   
5025742      396604       5025742        Closed      currency 1  2015-03-02   

         CREDIT_DAY_OVERDUE DAYS_CREDIT_ENDDATE DAYS_ENDDATE_FACT  \
5001071                   0          2016-03-01        2016-03-01   
5007519                   0          2015-08-31        2015-09-01   
5011980                   0          2016-04-09        2016-03-26   
5020085                   0          2035-03-01        2021-07-31   
5025742                   0          2016-04-01        2016-03-03   

         AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
5001071                     NaN                   0        193999.5   
5007519                     NaN                   0        127017.0   
5011980                     NaN                   0        470412.0   
5020085                     NaN                   0       2407500.0   
5025742                     0.0                   0         47617.2   

         AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
5001071                  0.0                   NaN                     0.0   
5007519                  NaN                   NaN                     0.0   
5011980                  0.0                   NaN                     0.0   
5020085                  0.0                   0.0                     0.0   
5025742                  0.0                   0.0                     0.0   

             CREDIT_TYPE  DAYS_CREDIT_UPDATE  AMT_ANNUITY  CNT_TRANSACTIONS  \
5001071  Consumer credit                 -60          NaN                 0   
5007519  Consumer credit               -2737          NaN                 0   
5011980  Consumer credit                -647          NaN                96   
5020085         Mortgage                 -32          NaN                 0   
5025742  Consumer credit               -2555      45000.0                11   

         CNT_DPD_91_120  CNT_DPD_1_30  CNT_DPD_61_90  CNT_DPD_120_PLUS  \
5001071               0             0              0                 0   
5007519               0             0              0                 0   
5011980               0             0              0                 0   
5020085               0             0              0                 0   
5025742               0             0              0                 0   

         CNT_DPD_31_60  CNT_NO_DPD _ft_last_time  
5001071              0           0    2015-03-02  
5007519              0           0    2015-03-02  
5011980              0          96    2023-02-02  
5020085              0           0    2015-03-02  
5025742              0          11    2016-01-02

In [ ]:
#@title Ratio of total

# feature_matrix,
feature_names = ft.dfs(entityset=es,
                        target_dataframe_name = 'curr_ids',
                        agg_primitives = ['sum'],
                        trans_primitives = ['divide_numeric'],
                        max_depth=2,
                        ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                        where_primitives=['sum'],
                        primitive_options={'divide_numeric':{'include_columns':{'bureau':['AMT_CREDIT_SUM_OVERDUE','AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_DEBT','AMT_CREDIT_SUM','AMT_CREDIT_MAX_OVERDUE','AMT_ANNUITY','CREDIT_TYPE','CREDIT_CURRENCY','CREDIT_ACTIVE']}},
                                            'count':{'include_columns':{'bureau':['AMT_CREDIT_SUM_OVERDUE','AMT_CREDIT_SUM_LIMIT','AMT_CREDIT_SUM_DEBT','AMT_CREDIT_SUM','AMT_CREDIT_MAX_OVERDUE','AMT_ANNUITY','CREDIT_TYPE','CREDIT_CURRENCY']}}},
                        verbose = True,features_only=True,
                       drop_contains=['bal'])
feature_names

Built 576 features


[<Feature: SUM(bureau.AMT_ANNUITY)>,
 <Feature: SUM(bureau.AMT_CREDIT_MAX_OVERDUE)>,
 <Feature: SUM(bureau.AMT_CREDIT_SUM)>,
 <Feature: SUM(bureau.AMT_CREDIT_SUM_DEBT)>,
 <Feature: SUM(bureau.AMT_CREDIT_SUM_LIMIT)>,
 <Feature: SUM(bureau.AMT_CREDIT_SUM_OVERDUE)>,
 <Feature: SUM(bureau.CNT_CREDIT_PROLONG)>,
 <Feature: SUM(bureau.CREDIT_DAY_OVERDUE)>,
 <Feature: SUM(bureau.DAYS_CREDIT_UPDATE)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Mortgage)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 1)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 2)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Microloan)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Closed)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Credit card)>,
 <Feature: SUM(bureau.AMT_ANNUITY WHERE CREDIT_ACTI

In [ ]:
# ft.graph_feature(feature_names[-1])
# ft.describe_feature(feature_names[-1])

'The result of the sum of the "AMT_ANNUITY" of all instances of "bureau" for each "SK_ID_CURR" in "curr_ids" divided by the sum of the "AMT_ANNUITY" of all instances of "bureau" where the "CREDIT_TYPE" is Mortgage for each "SK_ID_CURR" in "curr_ids".'

## GroupBy Features:

In [ ]:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      agg_primitives = [],
                                      trans_primitives = ['cum_max'],
                                      max_depth=3,
                                    #   ignore_dataframes=['bureau'],
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=[],
                                      groupby_trans_primitives=['cum_max'],
                                      verbose = True)
feature_names

Built 0 features


/usr/local/lib/python3.9/dist-packages/featuretools/synthesis/dfs.py:321: UnusedPrimitiveWarning: Some specified primitives were not used during DFS:
  trans_primitives: ['cum_max']
  groupby_trans_primitives: ['cum_max']
This may be caused by a using a value of max_depth that is too small, not setting interesting values, or it may indicate no compatible columns for the primitive were found in the data. If the DFS call contained multiple instances of a primitive in the list above, none of them were used.
  warnings.warn(warning_msg, UnusedPrimitiveWarning)


AssertionError: ignored

## DPD Features:

In [ ]:
#@title Max DPD in past 36 months

#This method can be used to know the maximum DPD a person has in a given period.
#So we can calculate Max DPD for variable timeframes (eg: 3M, 6M, 9M, ... 36M)

#Total amount of feature = (12 x 14) 168 + 12(entire duration) = 180

#We can also caluclate min, mean, median DPD for different timeframes too.

feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                      cutoff_time=pd.Timestamp('2023-03-02'),
                                      training_window='36 months',
                                      agg_primitives = ['max'],
                                      trans_primitives = [],
                                      max_depth=2,
                                    #   ignore_dataframes=['bureau'],
                                      primitive_options={'max':{'include_columns':{'bureau':[],'bal':['STATUS']}}},
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                      where_primitives=['max'],
                                    #   features_only=True,
                                      verbose = True)
feature_matrix.head()

Built 14 features
Elapsed: 00:03 | Progress: 100%|██████████


MAX(bal.STATUS)  \
SK_ID_CURR                    
233681                  0.0   
282475                  NaN   
421709                  NaN   
238338                  0.0   
230468                  0.0   

            MAX(bal.STATUS WHERE bureau.CREDIT_ACTIVE = Closed)  \
SK_ID_CURR                                                        
233681                                                    0.0     
282475                                                    NaN     
421709                                                    NaN     
238338                                                    0.0     
230468                                                    0.0     

            MAX(bal.STATUS WHERE bureau.CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                        
233681                                                    NaN     
282475                                                    NaN     
421709                                                    NaN     
238338                                                    NaN     
230468                                                    NaN     

            MAX(bal.STATUS WHERE bureau.CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                          
233681                                                    NaN       
282475                                                    NaN       
421709                                                    NaN       
238338                                                    NaN       
230468                                                    NaN       

            MAX(bal.STATUS WHERE bureau.CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                              
233681                                                    NaN           
282475                                                    NaN           
421709                                                    NaN           
238338                                                    NaN           
230468                                                    NaN           

            MAX(bal.STATUS WHERE bureau.CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                           
233681                                                    NaN        
282475                                                    NaN        
421709                                                    NaN        
238338                                                    NaN        
230468                                                    NaN        

            MAX(bal.STATUS WHERE bureau.CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                               
233681                                                    0.0            
282475                                                    NaN            
421709                                                    NaN            
238338                                                    0.0            
230468                                                    0.0            

            MAX(bal.STATUS WHERE bureau.CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                                      
233681                                                    NaN   
282475                                                    NaN   
421709                                                    NaN   
238338                                                    NaN   
230468                                                    NaN   

            MAX(bal.STATUS WHERE bureau.CREDIT_ACTIVE = Active)  \
SK_ID_CURR                                                        
233681                                                    0.0     
282475                                                    NaN     
421709                                                    NaN     
238338                                                   

In [ ]:
feature_matrix,feature_names = ft.dfs(entityset=es,
                                      target_dataframe_name = 'curr_ids',
                                    #   cutoff_time=pd.Timestamp('2023-03-02'),
                                    #   training_window='36 months',
                                      agg_primitives = ['max'],
                                      trans_primitives = [ft.primitives.RollingMax(40)],
                                      max_depth=2,
                                    #   ignore_dataframes=['bureau'],
                                    #   primitive_options={'max':{'include_columns':{'bureau':[],'bal':['STATUS']}}},
                                      ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                    #   where_primitives=['max'],
                                    #   features_only=True,
                                      verbose = True)
feature_matrix.head()

Built 28 features
Elapsed: 28:25 | Progress: 100%|██████████


MAX(bureau.AMT_ANNUITY)  MAX(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
276069                      5382.00                              5472.0   
153562                          NaN                                 NaN   
291125                         0.00                                 NaN   
142770                     10770.48                                 0.0   
361140                      5850.00                                 0.0   

            MAX(bureau.AMT_CREDIT_SUM)  MAX(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
276069                        554400.0                         247954.5   
153562                        224572.5                              0.0   
291125                         85500.0                              0.0   
142770                       1399500.0                         202801.5   
361140                       2106000.0                         362938.5   

            MAX(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
276069                              554400.0   
153562                                   0.0   
291125                                   NaN   
142770                                   0.0   
361140                                   0.0   

            MAX(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
276069                                     0.0   
153562                                     0.0   
291125                                     0.0   
142770                                     0.0   
361140                                     0.0   

            MAX(bureau.CNT_CREDIT_PROLONG)  MAX(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                                   
276069                                 1.0                             0.0   
153562                                 0.0                             0.0   
291125                                 0.0                             0.0   
142770                                 0.0                             0.0   
361140                                 0.0                             0.0   

            MAX(bureau.DAYS_CREDIT_UPDATE)  MAX(bal.STATUS)  \
SK_ID_CURR                                                    
276069                               -14.0             60.0   
153562                              -672.0              NaN   
291125                               -31.0              0.0   
142770                                -2.0              0.0   
361140                               -13.0              0.0   

            MAX(bureau.ROLLING_MAX(DAYS_CREDIT, AMT_ANNUITY, window_length=40))  \
SK_ID_CURR                                                                        
276069                                               128259.0                     
153562                                                16233.3                     
291125                                               261940.5                     
142770                                               319738.5                     
361140                                                59499.0                     

            MAX(bureau.ROLLING_MAX(DAYS_CREDIT, AMT_CREDIT_MAX_OVERDUE, window_length=40))  \
SK_ID_CURR                                                                                   
276069                                                41269.5                                
153562                                                    0.0                                
291125                                                12190.5                                
142770                                              5755815.0                                
361140                                                49558.5                                

            MAX(bureau.ROLLING_MAX(DAYS_CR

## Other Useful Primitives:

- mathematical operators(sum, difference, multiply, division, square root)

In [ ]:
#@title Median

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['Median'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['median'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 280 features
Elapsed: 00:03 | Progress:  48%|████▊     

/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/p

Elapsed: 00:03 | Progress:  76%|███████▌  

/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/p

Elapsed: 00:03 | Progress:  95%|█████████▍

/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/python3.9/dist-packages/numpy/lib/nanfunctions.py:1216: RuntimeWarning: Mean of empty slice
  return np.nanmean(a, axis, out=out, keepdims=keepdims)
/usr/local/lib/p

Elapsed: 00:04 | Progress: 100%|██████████


MEDIAN(bureau.AMT_ANNUITY)  MEDIAN(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                      
161736                             NaN                                    0.0   
437541                           220.5                                    0.0   
448677                             NaN                                    0.0   
158719                             NaN                                    0.0   
155214                             NaN                                    0.0   

            MEDIAN(bureau.AMT_CREDIT_SUM)  MEDIAN(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                      
161736                           87750.00                            35275.50   
437541                           55975.50                                0.00   
448677                          396110.25                           599893.38   
158719                           90000.00                                0.00   
155214                           41976.00                                0.00   

            MEDIAN(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                        
161736                                     0.00   
437541                                     0.00   
448677                                 75106.62   
158719                                     0.00   
155214                                     0.00   

            MEDIAN(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                          
161736                                        0.0   
437541                                        0.0   
448677                                        0.0   
158719                                        0.0   
155214                                        0.0   

            MEDIAN(bureau.CNT_CREDIT_PROLONG)  \
SK_ID_CURR                                      
161736                                    0.0   
437541                                    0.0   
448677                                    0.5   
158719                                    0.0   
155214                                    0.0   

            MEDIAN(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                      
161736                                    0.0   
437541                                    0.0   
448677                                    0.0   
158719                                    0.0   
155214                                    0.0   

            MEDIAN(bureau.DAYS_CREDIT_UPDATE)  MEDIAN(bal.STATUS)  \
SK_ID_CURR                                                          
161736                                  -34.0                 NaN   
437541                                 -450.0                 0.0   
448677                                 -909.5                 NaN   
158719                                 -609.0                 NaN   
155214                                 -848.0                 NaN   

            MEDIAN(bureau.AMT_ANNUITY WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                                                                  
161736                                                    NaN               
437541                                                    NaN               
448677                                                    NaN               
158719                                                    NaN               
155214                                                    NaN               

            MEDIAN(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                                          
161736                                                    NaN       
437541                                                    NaN       
448677                                                    NaN       
158719                                                    NaN       
155214              

In [ ]:
#@title PercentTrue

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['percent_true'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['percent_true'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 0 features


AssertionError: ignored

In [ ]:
#@title NumUnique

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['num_unique'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['num_unique'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 58 features
Elapsed: 00:00 | Progress: 100%|██████████


NUM_UNIQUE(bureau.CREDIT_ACTIVE)  \
SK_ID_CURR                                     
161736                                     2   
437541                                     2   
448677                                     2   
158719                                     2   
155214                                     2   

            NUM_UNIQUE(bureau.CREDIT_CURRENCY)  \
SK_ID_CURR                                       
161736                                       1   
437541                                       1   
448677                                       1   
158719                                       1   
155214                                       1   

            NUM_UNIQUE(bureau.CREDIT_TYPE)  \
SK_ID_CURR                                   
161736                                   2   
437541                                   2   
448677                                   2   
158719                                   2   
155214                                   3   

            NUM_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = currency 3)  \
SK_ID_CURR                                                                        
161736                                                   <NA>                     
437541                                                   <NA>                     
448677                                                   <NA>                     
158719                                                   <NA>                     
155214                                                   <NA>                     

            NUM_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Credit card)  \
SK_ID_CURR                                                                     
161736                                                      1                  
437541                                                      1                  
448677                                                      1                  
158719                                                      1                  
155214                                                      2                  

            NUM_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Microloan)  \
SK_ID_CURR                                                                   
161736                                                   <NA>                
437541                                                   <NA>                
448677                                                   <NA>                
158719                                                   <NA>                
155214                                                   <NA>                

            NUM_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_TYPE = Mortgage)  \
SK_ID_CURR                                                                  
161736                                                   <NA>               
437541                                                   <NA>               
448677                                                   <NA>               
158719                                                   <NA>               
155214                                                      1               

            NUM_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = currency 4)  \
SK_ID_CURR                                                                        
161736                                                   <NA>                     
437541                                                   <NA>                     
448677                                                   <NA>                     
158719                                                   <NA>                     
155214                                                   <NA>                     

            NUM_UNIQUE(bureau.CREDIT_ACTIVE WHERE CREDIT_CURRENCY = currency 2)  \
SK_ID_CURR                                                                        
161736                 

In [ ]:
#@title MaxMinDelta

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['max_min_delta'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['max_min_delta'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 19 features
Elapsed: 00:03 | Progress: 100%|██████████


MAX_MIN_DELTA(bureau.AMT_ANNUITY)  \
SK_ID_CURR                                      
217867                                11439.0   
386110                                 6390.0   
245209                                    0.0   
286017                                    0.0   
371986                                    0.0   

            MAX_MIN_DELTA(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                 
217867                                               0.0   
386110                                               0.0   
245209                                               0.0   
286017                                               0.0   
371986                                               0.0   

            MAX_MIN_DELTA(bureau.AMT_CREDIT_SUM)  \
SK_ID_CURR                                         
217867                                  342607.5   
386110                                  559629.0   
245209                                 1113615.0   
286017                                       0.0   
371986                                 1395000.0   

            MAX_MIN_DELTA(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                              
217867                                       309847.5   
386110                                            0.0   
245209                                        40059.0   
286017                                            0.0   
371986                                      1206765.0   

            MAX_MIN_DELTA(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                               
217867                                             0.0   
386110                                             0.0   
245209                                             0.0   
286017                                             0.0   
371986                                             0.0   

            MAX_MIN_DELTA(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                                 
217867                                               0.0   
386110                                               0.0   
245209                                               0.0   
286017                                               0.0   
371986                                               0.0   

            MAX_MIN_DELTA(bureau.CNT_CREDIT_PROLONG)  \
SK_ID_CURR                                             
217867                                           0.0   
386110                                           0.0   
245209                                           0.0   
286017                                           0.0   
371986                                           0.0   

            MAX_MIN_DELTA(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                             
217867                                           0.0   
386110                                           0.0   
245209                                           0.0   
286017                                           0.0   
371986                                           0.0   

            MAX_MIN_DELTA(bureau.DAYS_CREDIT_UPDATE)  \
SK_ID_CURR                                             
217867                                        1871.0   
386110                                        2093.0   
245209                                        2243.0   
286017                                           0.0   
371986                                         508.0   

            MAX_MIN_DELTA(bal.STATUS)  MAX_MIN_DELTA(bal.bureau.AMT_ANNUITY)  \
SK_ID_CURR                                                                     
217867                           30.0                                11439.0   
386110                           30.0                                 6390.0   
245209                            0.0                                    0.0   
286017                           30.0                                    0.

In [ ]:
#@title NMostCommonFrequency

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['n_most_common_frequency'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['n_most_common_frequency'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix()

In [ ]:
#@title PercentUnique

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['percent_unique'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['percent_unique'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

In [ ]:
#@title DateFirstEvent

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['date_first_event'],
                                       trans_primitives=[],
                                       max_depth=3,
                                       where_primitives=['date_first_event'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 0 features


AssertionError: ignored

In [ ]:
#@title Trend

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['trend'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['trend'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

In [ ]:
# We can also create trend variables for different timeframes too...

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       cutoff_time='2023-03-02',
                                       training_window='2 months',
                                       agg_primitives=['trend'],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=['trend'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 420 features
Elapsed: 00:03 | Progress: 100%|██████████


TREND(bureau.AMT_ANNUITY, DAYS_CREDIT)  \
SK_ID_CURR                                           
217867                                    6.176511   
386110                                         NaN   
245209                                         NaN   
286017                                         NaN   
371986                                         NaN   

            TREND(bureau.AMT_CREDIT_MAX_OVERDUE, DAYS_CREDIT)  \
SK_ID_CURR                                                      
217867                                                    NaN   
386110                                                    NaN   
245209                                                    NaN   
286017                                                    NaN   
371986                                                    NaN   

            TREND(bureau.AMT_CREDIT_SUM, DAYS_CREDIT)  \
SK_ID_CURR                                              
217867                                      216.69297   
386110                                            NaN   
245209                                            NaN   
286017                                            NaN   
371986                                            NaN   

            TREND(bureau.AMT_CREDIT_SUM_DEBT, DAYS_CREDIT)  \
SK_ID_CURR                                                   
217867                                          221.441402   
386110                                                 NaN   
245209                                                 NaN   
286017                                                 NaN   
371986                                                 NaN   

            TREND(bureau.AMT_CREDIT_SUM_LIMIT, DAYS_CREDIT)  \
SK_ID_CURR                                                    
217867                                                  NaN   
386110                                                  NaN   
245209                                                  NaN   
286017                                                  NaN   
371986                                                  NaN   

            TREND(bureau.AMT_CREDIT_SUM_OVERDUE, DAYS_CREDIT)  \
SK_ID_CURR                                                      
217867                                                    0.0   
386110                                                    NaN   
245209                                                    NaN   
286017                                                    NaN   
371986                                                    NaN   

            TREND(bureau.CNT_CREDIT_PROLONG, DAYS_CREDIT)  \
SK_ID_CURR                                                  
217867                                                0.0   
386110                                                NaN   
245209                                                NaN   
286017                                                NaN   
371986                                                NaN   

            TREND(bureau.CREDIT_DAY_OVERDUE, DAYS_CREDIT)  \
SK_ID_CURR                                                  
217867                                                0.0   
386110                                                NaN   
245209                                                NaN   
286017                                                NaN   
371986                                                NaN   

            TREND(bureau.DAYS_CREDIT_UPDATE, DAYS_CREDIT)  \
SK_ID_CURR                                                  
217867                                           1.484229   
386110                                                NaN   
245209                                                NaN   
286017                                                NaN   
371986                                                NaN   

            TREND(bal.STATUS, MONTHS_BALANCE)  \
SK_ID_CURR                                      
217867                                    0.0   
386110       

In [ ]:
#@title AvgTimeBetween

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=[ft.primitives.AvgTimeBetween(unit='days')],
                                       trans_primitives=[],
                                       max_depth=2,
                                       where_primitives=[ft.primitives.AvgTimeBetween(unit='days')],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 42 features
Elapsed: 00:00 | Progress: 100%|██████████


AVG_TIME_BETWEEN(bureau.DAYS_CREDIT, unit=days)  \
SK_ID_CURR                                                    
217867                                           480.000000   
386110                                           349.800000   
245209                                           288.428571   
286017                                                  NaN   
371986                                           150.333333   

            AVG_TIME_BETWEEN(bal.MONTHS_BALANCE, unit=days)  \
SK_ID_CURR                                                    
217867                                            11.259669   
386110                                            13.276243   
245209                                                  NaN   
286017                                            30.418605   
371986                                                  NaN   

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Bad debt, unit=days)  \
SK_ID_CURR                                                                                   
217867                                                    NaN                                
386110                                                    NaN                                
245209                                                    NaN                                
286017                                                    NaN                                
371986                                                    NaN                                

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_CURRENCY = currency 4, unit=days)  \
SK_ID_CURR                                                                                       
217867                                                    NaN                                    
386110                                                    NaN                                    
245209                                                    NaN                                    
286017                                                    NaN                                    
371986                                                    NaN                                    

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_TYPE = Credit card, unit=days)  \
SK_ID_CURR                                                                                    
217867                                                    NaN                                 
386110                                                    NaN                                 
245209                                                  673.0                                 
286017                                                    NaN                                 
371986                                                    NaN                                 

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_ACTIVE = Active, unit=days)  \
SK_ID_CURR                                                                                 
217867                                             371.000000                              
386110                                                    NaN                              
245209                                             421.666667                              
286017                                                    NaN                              
371986                                             222.000000                              

            AVG_TIME_BETWEEN(bureau.DAYS_CREDIT WHERE CREDIT_TYPE = Microloan, unit=days)  \
SK_ID_CURR                                                                                  
217867                                                    NaN                               
386110                                                    NaN                               
245209                                                    NaN                               
286017

In [ ]:
#@title TimeSinceLastMax

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=[ft.primitives.TimeSinceLastMax()],
                                       trans_primitives=[],
                                       max_depth=1,
                                       where_primitives=[ft.primitives.TimeSinceLastMax()],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

Built 126 features
Elapsed: 00:00 | Progress: 100%|██████████


TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, AMT_ANNUITY)  \
SK_ID_CURR                                                         
394426                                           0.000000e+00      
176244                                           0.000000e+00      
105016                                           0.000000e+00      
131214                                           0.000000e+00      
208567                                           2.541923e+07      

            TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                    
394426                                           1.790243e+07                 
176244                                           9.073763e+07                 
105016                                           2.383088e+08                 
131214                                           4.771043e+07                 
208567                                           4.019363e+07                 

            TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, AMT_CREDIT_SUM)  \
SK_ID_CURR                                                            
394426                                           2.274083e+07         
176244                                           3.751523e+07         
105016                                           1.081040e+08         
131214                                           4.771043e+07         
208567                                           2.541923e+07         

            TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                 
394426                                           2.274083e+07              
176244                                           3.751523e+07              
105016                                           1.081040e+08              
131214                                           4.771043e+07              
208567                                           2.541923e+07              

            TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                                                  
394426                                           2.274083e+07               
176244                                           1.180400e+08               
105016                                           1.649552e+08               
131214                                           1.919120e+08               
208567                                           4.019363e+07               

            TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                                                    
394426                                           2.274083e+07                 
176244                                           1.289264e+08                 
105016                                           2.383088e+08                 
131214                                           4.771043e+07                 
208567                                           4.019363e+07                 

            TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, CNT_CREDIT_PROLONG)  \
SK_ID_CURR                                                                
394426                                           2.274083e+07             
176244                                           1.289264e+08             
105016                                           2.379632e+08             
131214                                           1.983920e+08             
208567                                           4.019363e+07             

            TIME_SINCE_LAST_MAX(bureau.DAYS_CREDIT, CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                                
394426                                           2.274083e+07             
176244                                           1.289264e+08             
105016                        

In [ ]:
es['bureau'].head()

SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY DAYS_CREDIT  \
5001071      289470       5001071        Closed      currency 1  2015-03-02   
5007519      195162       5007519        Closed      currency 1  2015-03-02   
5011980      282691       5011980        Closed      currency 1  2015-03-02   
5020085      426357       5020085        Closed      currency 1  2015-03-02   
5025742      396604       5025742        Closed      currency 1  2015-03-02   

         CREDIT_DAY_OVERDUE DAYS_CREDIT_ENDDATE DAYS_ENDDATE_FACT  \
5001071                   0          2016-03-01        2016-03-01   
5007519                   0          2015-08-31        2015-09-01   
5011980                   0          2016-04-09        2016-03-26   
5020085                   0          2035-03-01        2021-07-31   
5025742                   0          2016-04-01        2016-03-03   

         AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
5001071                     NaN                   0        193999.5   
5007519                     NaN                   0        127017.0   
5011980                     NaN                   0        470412.0   
5020085                     NaN                   0       2407500.0   
5025742                     0.0                   0         47617.2   

         AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
5001071                  0.0                   NaN                     0.0   
5007519                  NaN                   NaN                     0.0   
5011980                  0.0                   NaN                     0.0   
5020085                  0.0                   0.0                     0.0   
5025742                  0.0                   0.0                     0.0   

             CREDIT_TYPE  DAYS_CREDIT_UPDATE  AMT_ANNUITY  CNT_TRANSACTIONS  \
5001071  Consumer credit                 -60          NaN                 0   
5007519  Consumer credit               -2737          NaN                 0   
5011980  Consumer credit                -647          NaN                96   
5020085         Mortgage                 -32          NaN                 0   
5025742  Consumer credit               -2555      45000.0                11   

         CNT_DPD_91_120  CNT_DPD_1_30  CNT_DPD_61_90  CNT_DPD_120_PLUS  \
5001071               0             0              0                 0   
5007519               0             0              0                 0   
5011980               0             0              0                 0   
5020085               0             0              0                 0   
5025742               0             0              0                 0   

         CNT_DPD_31_60  CNT_NO_DPD _ft_last_time  
5001071              0           0    2015-03-02  
5007519              0           0    2015-03-02  
5011980              0          96    2023-02-02  
5020085              0           0    2015-03-02  
5025742              0          11    2016-01-02

In [ ]:
#@title DistanceToHoliday

feature_matrix, feature_names = ft.dfs(entityset=es,
                                       target_dataframe_name='curr_ids',
                                       agg_primitives=['max'],
                                       trans_primitives=[ft.primitives.DistanceToHoliday(holiday='Diwali',country='IN')],
                                       max_depth=2,
                                       where_primitives=['max'],
                                       ignore_columns={'bureau':['CNT_TRANSACTIONS', 'CNT_DPD_91_120', 'CNT_DPD_1_30','CNT_DPD_61_90', 'CNT_DPD_120_PLUS', 'CNT_DPD_31_60', 'CNT_NO_DPD']},
                                       verbose=True)
feature_matrix

/usr/local/lib/python3.10/dist-packages/holidays/countries/india.py:106: Warning: Diwali and Holi holidays available from 2001 to 2030 only
  warnings.warn(warning_msg, Warning)


Built 308 features
Elapsed: 00:01 | Progress: 100%|██████████


MAX(bureau.AMT_ANNUITY)  MAX(bureau.AMT_CREDIT_MAX_OVERDUE)  \
SK_ID_CURR                                                                
434360                          NaN                            26960.04   
316718                      72823.5                                0.00   
315266                          NaN                                0.00   
320673                       7978.5                                0.00   
403530                          NaN                                 NaN   

            MAX(bureau.AMT_CREDIT_SUM)  MAX(bureau.AMT_CREDIT_SUM_DEBT)  \
SK_ID_CURR                                                                
434360                     2133000.000                      1752528.645   
316718                     7200000.000                       164668.500   
315266                      195251.175                            0.000   
320673                      225000.000                       224491.500   
403530                      180000.000                              NaN   

            MAX(bureau.AMT_CREDIT_SUM_LIMIT)  \
SK_ID_CURR                                     
434360                               31500.0   
316718                                   0.0   
315266                                   0.0   
320673                                   0.0   
403530                                   NaN   

            MAX(bureau.AMT_CREDIT_SUM_OVERDUE)  \
SK_ID_CURR                                       
434360                                     0.0   
316718                                     0.0   
315266                                     0.0   
320673                                     0.0   
403530                                     0.0   

            MAX(bureau.CNT_CREDIT_PROLONG)  MAX(bureau.CREDIT_DAY_OVERDUE)  \
SK_ID_CURR                                                                   
434360                                 1.0                             0.0   
316718                                 0.0                             0.0   
315266                                 0.0                             0.0   
320673                                 0.0                             0.0   
403530                                 0.0                             0.0   

            MAX(bureau.DAYS_CREDIT_UPDATE)  MAX(bal.STATUS)  \
SK_ID_CURR                                                    
434360                                -5.0              NaN   
316718                                -8.0             30.0   
315266                              -145.0              NaN   
320673                                -8.0             30.0   
403530                               -15.0              NaN   

            MAX(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Bad debt)  \
SK_ID_CURR                                                           
434360                                                    NaN        
316718                                                    NaN        
315266                                                    NaN        
320673                                                    NaN        
403530                                                    NaN        

            MAX(bureau.AMT_ANNUITY WHERE CREDIT_TYPE = Consumer credit)  \
SK_ID_CURR                                                                
434360                                                    NaN             
316718                                                11781.0             
315266                                                    NaN             
320673                                                    0.0             
403530                                                    NaN             

            MAX(bureau.AMT_ANNUITY WHERE CREDIT_ACTIVE = Sold)  \
SK_ID_CURR                                                       
434360                                                    NaN    
316718                                                    NaN    
31